## Using Tutorial from 

https://towardsdatascience.com/how-to-generate-music-using-a-lstm-neural-network-in-keras-68786834d4c5

In [1]:
from music21 import converter, instrument, note, chord, stream
import glob
import numpy as np
from keras.models import Sequential
from keras.layers import Dense, LSTM, Dropout
from keras.callbacks import EarlyStopping, ModelCheckpoint
import tensorflow as tf
from tqdm import tqdm
np.random.seed(100)
tf.set_random_seed(100)

Using TensorFlow backend.


In [2]:
notes = []
for file in glob.glob('./midi/*'):
    music = converter.parse(file)
    parts = instrument.partitionByInstrument(music)
    if parts:
        notes_to_parse = parts.parts[0].recurse()
    else:
        notes_to_parse = music.flat.notes
    for element in notes_to_parse:
        if isinstance(element, note.Note):
            notes.append(str(element.pitch))
        elif isinstance(element, chord.Chord):
            notes.append('.'.join(str(n) for n in element.normalOrder))
    print(file,' Complete')

./midi\appass_1.mid  Complete
./midi\appass_2.mid  Complete
./midi\appass_3.mid  Complete
./midi\bach_846.mid  Complete
./midi\bach_847.mid  Complete
./midi\bach_850.mid  Complete
./midi\beethoven_hammerklavier_1.mid  Complete
./midi\beethoven_hammerklavier_2.mid  Complete
./midi\beethoven_hammerklavier_3.mid  Complete
./midi\beethoven_hammerklavier_4.mid  Complete
./midi\beethoven_les_adieux_1.mid  Complete
./midi\beethoven_les_adieux_2.mid  Complete
./midi\beethoven_les_adieux_3.mid  Complete
./midi\beethoven_opus10_1.mid  Complete
./midi\beethoven_opus10_2.mid  Complete
./midi\beethoven_opus10_3.mid  Complete
./midi\beethoven_opus22_1.mid  Complete
./midi\beethoven_opus22_2.mid  Complete
./midi\beethoven_opus22_3.mid  Complete
./midi\beethoven_opus22_4.mid  Complete
./midi\beethoven_opus90_1.mid  Complete
./midi\beethoven_opus90_2.mid  Complete
./midi\elise.mid  Complete
./midi\grieg_album.mid  Complete
./midi\grieg_berceuse.mid  Complete
./midi\grieg_brooklet.mid  Complete
./midi\g

In [3]:
len(notes)

192768

In [4]:
seq_n = 10
pitchnames = sorted(set(item for item in notes))
note_to_int = dict((note, number) for number, note in enumerate(pitchnames))
print(note_to_int)

{'8.10.0.3': 209, 'E5': 287, 'F3': 299, '3.5.9': 115, '1.4.6': 35, '1.4.7.10': 37, '5.7': 150, 'E-2': 277, '3.4': 108, '7.11.1': 193, '1.4': 34, '7': 183, 'D3': 271, '6.9': 176, 'C#4': 259, '6.11.0': 168, '7.10.0': 186, '6': 163, '0.3': 9, 'F#3': 292, '6.9.0': 177, 'A2': 240, '3.7.11': 123, '8': 202, '0.3.5.8': 11, '6.9.11': 181, 'F6': 302, '3.6.9.11': 120, '8.1': 207, '3.7.10': 122, '1.3': 28, '5': 145, '7.9': 198, '11.2.4': 75, '9.1.4': 228, 'E2': 284, '11.2': 73, '0.2': 4, '0.4': 16, '7.10': 185, '1.2.5.8': 26, '9.11': 232, 'B2': 252, '2.6': 99, 'C3': 265, '7.8.10.1.3': 197, '0.4.5': 17, '9.11.2.5': 235, '9.0.3.5': 224, '3.8': 125, 'C4': 266, 'E-4': 279, '6.8': 172, '2.7.8': 105, '10.2.3': 60, '8.10.11': 211, '11.0': 66, '0.2.7': 8, 'F#7': 296, '1.4.8': 39, 'B-1': 245, '0.6': 22, '10.1.3.6': 53, '8.9': 218, '7.9.1': 201, '2.4.9': 91, '6.7.10': 170, '11.3': 80, '11.0.2.5.7': 67, '4.6.9': 134, '4.6': 132, 'E-1': 276, '7.0': 184, '10.2.5': 63, '11.1.5': 72, '8.10.2': 212, '11.2.5': 77,

In [5]:
network_inp = []
network_out = []

for i in range(len(notes) - seq_n):
    seq_in = notes[i:i + seq_n]
    seq_out = notes[i + seq_n]
    network_inp.append([note_to_int[char] for char in seq_in])
    network_out.append(note_to_int[seq_out])

In [6]:
n_patterns = len(network_inp)
n_vocab = len(note_to_int)

In [7]:
print(n_patterns)
print(n_vocab)

192758
316


In [8]:
network_inp = np.reshape(network_inp, (n_patterns, seq_n, 1))
network_inp = network_inp / float(n_vocab)
print(network_inp.shape)
network_out = np.eye(n_vocab)[network_out]
print(network_out.shape)

(192758, 10, 1)
(192758, 316)


In [9]:
filepath = './weights_best.hdf5'

In [11]:
model = Sequential()
model.add(LSTM(256, input_shape = (network_inp.shape[1], network_inp.shape[2]), 
               return_sequences = True))
model.add(Dropout(0.3))
model.add(LSTM(256))
model.add(Dense(256))
model.add(Dropout(0.3))
model.add(Dense(n_vocab, activation='softmax'))
callbacks = [EarlyStopping(monitor='loss', patience=10, verbose=0, mode='auto'), 
             ModelCheckpoint(filepath=filepath, monitor='loss', verbose=0, mode='max')]
model.compile(loss = 'categorical_crossentropy', optimizer='rmsprop')
model.load_weights('weights_best.hdf5')

In [26]:
model.fit(network_inp, network_out, epochs=250, batch_size=32, verbose=1, callbacks=callbacks)

Epoch 1/250
14503/14503 [==============================] - ETA: 745s - loss: 5.4337 - ETA: 383s - loss: 5.4247 - ETA: 200s - loss: 5.3138 - ETA: 164s - loss: 5.3958 - ETA: 123s - loss: 5.3717 - ETA: 99s - loss: 5.2997  - ETA: 92s - loss: 5.2569 - ETA: 79s - loss: 5.2142 - ETA: 71s - loss: 5.1725 - ETA: 64s - loss: 5.1417

In [12]:
start = np.random.randint(0, len(network_inp) - 1)
int_to_note = dict((number, note) for number, note in enumerate(pitchnames))

pattern = network_inp[start].reshape((seq_n))
pattern = pattern.tolist()
prediction_output = []

for note_index in tqdm(range(14386)):
    prediction_input = np.reshape(pattern, (1, len(pattern), 1))
    prediction = model.predict(prediction_input, verbose=1)

    index = np.argmax(prediction)
    result = int_to_note[index]
    prediction_output.append(result)

    pattern.append(index / n_vocab)
    pattern = [x for x in pattern]
    pattern = pattern[1:len(pattern)+1]

  0%|                                                                                        | 0/14386 [00:00<?, ?it/s]

1/1 [==============================] - 0s


  0%|                                                                              | 1/14386 [00:00<3:15:23,  1.23it/s]

1/1 [==============================] - 0s


  0%|                                                                              | 8/14386 [00:00<2:17:53,  1.74it/s]

...

100%|███████████████████████████████████████████████████████████████████████████▉| 14373/14386 [04:17<00:00, 56.99it/s]

1/1 [==============================] - 0s


100%|███████████████████████████████████████████████████████████████████████████▉| 14380/14386 [04:17<00:00, 58.32it/s]

1/1 [==============================] - 0s


100%|████████████████████████████████████████████████████████████████████████████| 14386/14386 [04:17<00:00, 55.91it/s]


In [13]:
prediction_output[14000:14100]

['B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2',
 'B-2',
 'A5',
 'A2',
 'B-2']

In [14]:
offset = 0
output_notes = []

# create note and chord objects based on the values generated by the model

for pattern in prediction_output:
    # pattern is a chord
    if ('.' in pattern) or pattern.isdigit():
        notes_in_chord = pattern.split('.')
        notes = []
        for current_note in notes_in_chord:
            new_note = note.Note(int(current_note))
            new_note.storedInstrument = instrument.Piano()
            notes.append(new_note)
        new_chord = chord.Chord(notes)
        new_chord.offset = offset
        output_notes.append(new_chord)
    # pattern is a note
    else:
        new_note = note.Note(pattern)
        new_note.offset = offset
        new_note.storedInstrument = instrument.Piano()
        output_notes.append(new_note)

    # increase offset each iteration so that notes do not stack
    offset += 0.5

In [15]:
midi_stream = stream.Stream(output_notes)

midi_stream.write('midi', fp='test_output.mid')

'test_output.mid'